In [1]:
import json
import numpy as np
from typing import Tuple, Literal, Union, Optional, List, Dict, NamedTuple, Callable, Any, Set
import plotly.graph_objs as go
import plotly.express as px
import pandas as pd
import pickle
import os
import math
import random
from eoh.problems.optimization.classic_benchmark_path_planning.utils.benchmark import MultiMapBenchmarker
import warnings
import types
import sys

In [3]:
class Map(NamedTuple):
    grid: np.ndarray
    start: Union[Tuple[float, float], Tuple[float, float, float]]
    goal: Union[Tuple[float, float], Tuple[float, float, float]]
    obstacles: List[Union[Tuple[float, float, float, float], Tuple[float, float, float, float, float, float]]] # x, y, width, height or x, y, z, width, height, dimension
    size: Union[Tuple[int, int], Tuple[int, int, int]]

class PlannerResult(NamedTuple):
    success: bool
    path: List[Union[Tuple[float, float], Tuple[float, float, float]]]
    nodes: List[Union[Tuple[float, float], Tuple[float, float, float]]]
    edges: List[Tuple[Tuple[float, ...], Tuple[float, ...]]]  # (parent, child)

class Node:
    def __init__(self, position, parent=None, cost=0.0):
        self.position = position
        self.parent = parent
        self.cost = cost
        self.children = []
        self.valid = True  # 장애물 충돌 여부 등


In [18]:
def visualize_map_shapes(
    map_array: np.ndarray,
    start: Optional[Tuple[int, ...]] = None,
    goal: Optional[Tuple[int, ...]] = None,
    obs:List[Tuple[int, ...]] = None,
    path: Optional[List[Tuple[float, ...]]] = None,
    nodes: Optional[List[Tuple[float, ...]]] = None,
    edges: Optional[List[Tuple[float, ...]]] = None,
    title: str = "Map Visualization"
):
    fig = go.Figure()

    if map_array.ndim == 2:
        height, width = map_array.shape
        
        for x, y, w, h in obs:
                fig.add_shape(
                    type="rect",
                    x0=x, x1=x+w, y0=y, y1=y+h,
                    fillcolor="purple",opacity=0.5,
                    line=dict(width=0)
                )

        # 방문 노드
        if nodes:
            vx, vy = zip(*nodes)
            fig.add_trace(go.Scatter(
                x=vx, y=vy, mode="markers",
                marker=dict(size=4, color="blue"),
                name="nodes"
            ))

        # 경로
        if path:
            px, py = zip(*path)
            fig.add_trace(go.Scatter(
                x=px, y=py, mode="lines+markers",
                line=dict(color="green"),
                marker=dict(size=6),
                name="Path"
            ))

        # 엣지 (연결 정보)
        if edges:
            for parent, child in edges:
                fig.add_trace(go.Scatter(
                    x=[parent.position[0], child.position[0]], y=[parent.position[1], child.position[1]],
                    mode="lines",
                    line=dict(color="lightblue", width=1),
                    showlegend=False,
                    hoverinfo="skip"
                ))


        # 시작/목표
        if start:
            fig.add_trace(go.Scatter(
                x=[start[0]], y=[start[1]], mode="markers",
                marker=dict(size=10, color="red"),
                name="Start"
            ))

        if goal:
            fig.add_trace(go.Scatter(
                x=[goal[0]], y=[goal[1]], mode="markers",
                marker=dict(size=10, color="orange"),
                name="Goal"
            ))

        fig.add_shape(
            type="rect",
            x0=0, y0=0,
            x1=width, y1=height,
            line=dict(color="white", width=3),
            fillcolor="rgba(0,0,0,0)",  # 투명 내부
            layer="above"
        )

        fig.update_layout(
            title=title,
            xaxis=dict(scaleanchor="y", showgrid=False),
            # yaxis=dict(showgrid=False, autorange="reversed"),
            yaxis=dict(showgrid=False),
            height=600, width=600
        )

    elif map_array.ndim == 3:
        z, y, x = map_array.nonzero()
        x, y, z = list(x), list(y), list(z)

        # for x,y,w,h in obs:
        #     fig.add_trace(go.Mesh3d(
        #         x=x, y=y, z=z,
        #         color='black',
        #         opacity=1.0,
        #         alphahull=0,
        #         name='Obstacles'
        #     ))

        fig.add_trace(go.Mesh3d(
            x=x, y=y, z=z,
            color='black',
            opacity=1.0,
            alphahull=0,
            name='Obstacles'
        ))

        if nodes:
            vx, vy, vz = zip(*nodes)
            fig.add_trace(go.Scatter3d(
                x=vx, y=vy, z=vz,
                mode='markers',
                marker=dict(size=2, color='blue'),
                name='Visited'
            ))

        # 엣지 (연결 정보)
        if edges:
            for parent, child in edges:
                fig.add_trace(go.Scatter3d(
                    x=[parent.position[0], child.position[0]],
                    y=[parent[1].position, child.position[1]],
                    z=[parent[2].position, child.position[2]],
                    mode='lines',
                    line=dict(color='lightblue', width=2),
                    showlegend=False,
                    hoverinfo="skip"
                ))

        if path:
            px_, py_, pz_ = zip(*path)
            fig.add_trace(go.Scatter3d(
                x=px_, y=py_, z=pz_,
                mode='lines+markers',
                marker=dict(size=3, color='green'),
                name='Path'
            ))

        if start:
            fig.add_trace(go.Scatter3d(
                x=[start[0]], y=[start[1]], z=[start[2]],
                mode='markers',
                marker=dict(size=5, color='red'),
                name='Start'
            ))

        if goal:
            fig.add_trace(go.Scatter3d(
                x=[goal[0]], y=[goal[1]], z=[goal[2]],
                mode='markers',
                marker=dict(size=5, color='orange'),
                name='Goal'
            ))

        fig.update_layout(
            title=title,
            scene=dict(aspectmode='data'),
            height=700, width=700
        )

        

    fig.show()


In [4]:
class MapIO:
    @staticmethod
    def save_map(map_data: Map, filename: str) -> None:
        """Save Map object to a binary file."""
        with open(filename, 'wb') as f:
            pickle.dump(map_data, f)

    @staticmethod
    def load_map(filename: str) -> Map:
        """Load Map object from a binary file."""
        if not os.path.exists(filename):
            raise FileNotFoundError(f"Map file not found: {filename}")
        with open(filename, 'rb') as f:
            return pickle.load(f)

In [41]:
raw_maps = ["Maze_map_easy.pkl", "Narrow_map.pkl", "Multi_obs_map.pkl"]

multi_obs_map = MapIO.load_map("Multi_obs_map.pkl")
print("Start:", multi_obs_map.start)
print("Obstacles:", len(multi_obs_map.obstacles))
print(multi_obs_map.grid.shape)

maze_map = MapIO.load_map("Maze_map_easy.pkl")
print("Start:", maze_map.start)
print("Obstacles:", len(maze_map.obstacles))
print(maze_map.grid.shape)

narrow_map = MapIO.load_map("Narrow_map.pkl")
print("Start:", narrow_map.start)
print("Obstacles:", len(narrow_map.obstacles))
print(narrow_map.grid.shape)

Start: (1, 1)
Obstacles: 35
(100, 100)
Start: (29, 10)
Obstacles: 5
(100, 100)
Start: (80, 50)
Obstacles: 5
(100, 100)


In [42]:
maps=[multi_obs_map, maze_map, narrow_map]

In [47]:
json_path = './eoh/src/eoh/problems/optimization/classic_benchmark_path_planning/utils/classic_method_.json'
with open(json_path, "r") as f:
    classic_method = json.load(f)

print(classic_method[0].keys())

dict_keys(['algorithm', 'algorithm_description', 'planning_mechanism', 'code'])


In [48]:
print([n['algorithm'] for n in classic_method])

['RRT', 'RRT*', 'RRT-Connect', 'RRT*-Connect', 'BI-RRT', 'BI-RRT*', 'Informed-RRT*', 'Improved-RRT*-Connect']


In [90]:
print(classic_method[2]['code'])


class Node:
    def __init__(self, position, parent=None, cost=0.0):
        self.position = position
        self.parent = parent
        self.cost = cost
        self.children = []
        self.valid = True

    def add_child(self, child):
        self.children.append(child)


class Planner:
    def __init__(self, max_iter: int = 5000, step_size: float = 5.0):
        self.max_iter = max_iter
        self.step_size = step_size

    def plan(self, map) -> PlannerResult:
        bounds = map.size
        start_position = map.start
        goal_position = map.goal
        obstacles = map.obstacles
        is_3d = len(bounds) == 3

        start_tree = [Node(start_position)]
        goal_tree = [Node(goal_position)]
        nodes = []
        edges = []
        success_state = False
        extracted_path = []

        for iter in range(self.max_iter):
            rand = self._sample_free(bounds, obstacles, is_3d)
            for tree_a, tree_b in [(start_tree, goal_tree), (goal_tree, s

In [72]:
import_string ='''
from typing import Tuple, Literal, Union, Optional, List, Dict, NamedTuple, Callable, Any, Set, TYPE_CHECKING, Type
import time
from queue import Queue
import numpy as np
import random
import math
import sys
import os
from eoh.problems.optimization.classic_benchmark_path_planning.utils.architecture_utils import PlannerResult, Map
'''

In [94]:
code_string = code
with warnings.catch_warnings():
    warnings.simplefilter("ignore")
    planning_module = types.ModuleType("planning_module")
    exec(import_string+code_string, planning_module.__dict__)
    sys.modules[planning_module.__name__] = planning_module
    p = planning_module.Planner(max_iter=5000)

In [97]:
for pmap in maps:
    result = p.plan(map=pmap)
    visualize_map_shapes(pmap.grid, obs=pmap.obstacles, start=pmap.start, goal=pmap.goal,
                        path=result.path, nodes=list(map(lambda x: x.position, result.nodes)), edges=result.edges)

In [68]:
json_path = './eoh/src/eoh/problems/optimization/classic_benchmark_path_planning/utils/classic_method_.json'

In [69]:
with open(json_path, "a") as f:
    json.dump(result, f, indent=4)
    f.write(",\n")

In [96]:
code = '''
class Node:
    def __init__(self, position, parent=None, cost=0.0):
        self.position = position        # Tuple[float, ...] → 2D: (x,y), 3D: (x,y,z)
        self.parent = parent            # Node or None
        self.cost = cost                # Path cost
        self.children = []
        self.valid = True               # For collision checking etc.

    def add_child(self, child_node):
        self.children.append(child_node)
        child_node.parent = self

    def remove_child(self, child_node):
        if child_node in self.children:
            self.children.remove(child_node)

    def path_from_root(self):
        path = []
        n = self
        while n is not None:
            path.append(n.position)
            n = n.parent
        return path[::-1]


class Planner:
    def __init__(self, max_iter: int = 5000, step_size: float=5.0):
        self.max_iter = max_iter
        self.step_size = step_size

    def plan(self, map) -> PlannerResult:
        import math, random, time

        bounds = map.size                  # Tuple[int, ...]: (W,H) or (W,H,D)
        start_position = map.start         # Tuple[float, ...] (W,H) or (W,H,D)
        goal_position = map.goal           # Tuple[float, ...] (W,H) or (W,H,D)
        obstacles = map.obstacles          # Rectangular/box obstacles
        is_3d = len(bounds) == 3

        # Core data
        success_state = False              # will be True only if finished without timeout
        extracted_path = []                # best path from start to goal
        nodes = []
        edges = []

        # Time limit (hard wall)
        start_time = time.time()
        TIME_LIMIT = 30.0
        timed_out = False

        # Root
        root = Node(start_position, parent=None, cost=0.0)
        nodes.append(root)
        tree = [root]

        # Heuristic constants
        c_min = self._euclid(start_position, goal_position)
        c_best = float("inf")
        best_goal_node = None

        # Cache rotation basis for informed sampling (depends only on start/goal)
        R_cached = None

        for it in range(self.max_iter):
            # Enforce time limit
            if time.time() - start_time > TIME_LIMIT:
                timed_out = True
                break

            # --- Sampling ---
            if c_best < float("inf"):
                if R_cached is None:
                    R_cached = self._orthonormal_basis(tuple((goal_position[d] - start_position[d]) / max(c_min,1e-12) for d in range(len(bounds))))
                sample = self._informed_sample(bounds, start_position, goal_position, c_min, c_best, is_3d, R_cached)
            else:
                sample = self._uniform_free_sample(bounds, obstacles, is_3d)

            # --- Nearest & Steer (clamped to bounds) ---
            nearest = min(tree, key=lambda n: self._euclid(n.position, sample))
            new_pos = self._steer_clamped(nearest.position, sample, bounds)

            # Bounds & collision checks
            if self._is_out_of_bounds(new_pos, bounds):
                continue
            if self._is_in_obstacle(new_pos, obstacles, is_3d):
                continue
            if self._is_edge_in_obstacle(nearest.position, new_pos, obstacles, is_3d, resolution=max(0.05, min(self.step_size/5.0, 0.3))):
                continue

            # --- Best parent selection (RRT*) ---
            neighbors = self._near_nodes(tree, new_pos, bounds)
            best_parent = nearest
            best_cost = nearest.cost + self._euclid(nearest.position, new_pos)
            for nb in neighbors:
                if not self._is_edge_in_obstacle(nb.position, new_pos, obstacles, is_3d, resolution=max(0.05, min(self.step_size/5.0, 0.3))):
                    cand = nb.cost + self._euclid(nb.position, new_pos)
                    if cand + 1e-12 < best_cost:
                        best_parent = nb
                        best_cost = cand

            new_node = Node(new_pos, parent=best_parent, cost=best_cost)
            best_parent.add_child(new_node)
            tree.append(new_node)
            nodes.append(new_node)
            edges.append((best_parent, new_node))

            # --- Rewire neighbors (RRT*) ---
            for nb in neighbors:
                if nb is best_parent:
                    continue
                new_cost_through = new_node.cost + self._euclid(new_node.position, nb.position)
                if new_cost_through + 1e-12 < nb.cost:
                    if not self._is_edge_in_obstacle(new_node.position, nb.position, obstacles, is_3d, resolution=max(0.05, min(self.step_size/5.0, 0.3))):
                        # update edge structure
                        if nb.parent is not None:
                            try:
                                edges.remove((nb.parent, nb))
                            except ValueError:
                                pass
                            nb.parent.remove_child(nb)
                        new_node.add_child(nb)
                        nb.cost = new_cost_through
                        edges.append((new_node, nb))

            # --- Try snap to goal ---
            if self._euclid(new_pos, goal_position) <= self.step_size:
                if (not self._is_in_obstacle(goal_position, obstacles, is_3d) and
                    not self._is_edge_in_obstacle(new_pos, goal_position, obstacles, is_3d, resolution=max(0.05, min(self.step_size/5.0, 0.3)))):
                    goal_node = Node(goal_position, parent=new_node, cost=new_node.cost + self._euclid(new_pos, goal_position))
                    new_node.add_child(goal_node)
                    tree.append(goal_node)
                    nodes.append(goal_node)
                    edges.append((new_node, goal_node))
                    # Update best solution
                    if goal_node.cost + 1e-12 < c_best:
                        c_best = goal_node.cost
                        best_goal_node = goal_node

            # Optional early smoothing if we have a solution and a bit of time
            if best_goal_node is not None and (time.time() - start_time) < TIME_LIMIT * 0.9:
                # Try a tiny amount of shortcut smoothing without exceeding time budget
                best_path = best_goal_node.path_from_root()
                best_path = self._shortcut_path(best_path, obstacles, is_3d, bounds, budget_sec=0.002, t0=start_time, limit=TIME_LIMIT)
                # If smoothing improved, we can reflect as a better c_best (approximate)
                if best_path and len(best_path) >= 2:
                    path_len = 0.0
                    for i in range(len(best_path)-1):
                        path_len += self._euclid(best_path[i], best_path[i+1])
                    if path_len + 1e-12 < c_best:
                        c_best = path_len

        # Prepare result
        if best_goal_node is not None:
            extracted_path = best_goal_node.path_from_root()
        else:
            extracted_path = []

        if timed_out:
            success_state = False  # indicate time limit reached (even if a path exists)
        else:
            success_state = best_goal_node is not None

        return PlannerResult(
            success=success_state,
            path=extracted_path,
            nodes=nodes,
            edges=edges
        )

    # ---------- Helpers ----------

    def _euclid(self, a, b):
        import math
        return math.dist(a, b)

    def _uniform_free_sample(self, bounds, obstacles, is_3d):
        import random
        # Rejection until outside obstacles & inside bounds
        while True:
            if is_3d:
                p = (random.uniform(0, bounds[0]),
                     random.uniform(0, bounds[1]),
                     random.uniform(0, bounds[2]))
            else:
                p = (random.uniform(0, bounds[0]),
                     random.uniform(0, bounds[1]))
            if not self._is_in_obstacle(p, obstacles, is_3d):
                return p

    def _informed_sample(self, bounds, start, goal, c_min, c_best, is_3d, R_cached=None):
        import math, random
        n = len(bounds)
        if c_best == float("inf"):
            return self._uniform_free_sample(bounds, [], is_3d)

        center = tuple((start[d] + goal[d]) * 0.5 for d in range(n))
        a = max(c_min * 0.5, c_best * 0.5)  # major semi-axis
        b_sq = a*a - (c_min*0.5)*(c_min*0.5)
        b = math.sqrt(max(0.0, b_sq))
        scales = [a] + [b]*(n-1)

        # Orthonormal basis with e1 aligned to start->goal
        if R_cached is None:
            e1 = tuple((goal[d] - start[d]) / max(c_min, 1e-12) for d in range(n))
            R = self._orthonormal_basis(e1)
        else:
            R = R_cached

        # Sample unit n-ball and map
        while True:
            u = [random.uniform(-1.0, 1.0) for _ in range(n)]
            if sum(ui*ui for ui in u) <= 1.0:
                # scale in local frame
                us = [u[i]*scales[i] for i in range(n)]
                x = self._matvec(R, us)
                samp = tuple(x[d] + center[d] for d in range(n))
                if not self._is_out_of_bounds(samp, bounds) and not self._is_in_obstacle(samp, [], is_3d=False):
                    return self._clamp_to_bounds(samp, bounds)

    def _near_nodes(self, tree, position, bounds):
        import math
        n = max(1, len(tree))
        dim = len(bounds)
        # Theoretical radius ~ gamma * (log n / n)^(1/d) with practical floors/ceilings
        gamma = max(1.0, 2.0 * sum(bounds) / max(1.0, dim))  # scale-aware
        r = gamma * ((math.log(n + 1) / (n + 1)) ** (1.0 / dim))
        r = max(self.step_size * 2.0, min(r, max(bounds)))    # clamp
        return [nd for nd in tree if self._euclid(nd.position, position) <= r]

    def _orthonormal_basis(self, e1):
        import math
        n = len(e1)
        norm = math.sqrt(sum(v*v for v in e1)) or 1.0
        e1n = [v / norm for v in e1]
        if n == 2:
            e2 = [-e1n[1], e1n[0]]
            return [e1n, e2]
        else:
            # pick non-collinear reference
            ref = [1.0, 0.0, 0.0] if abs(e1n[0]) < 0.9 else [0.0, 1.0, 0.0]
            dot = sum(ref[i]*e1n[i] for i in range(3))
            e2 = [ref[i] - dot*e1n[i] for i in range(3)]
            n2 = math.sqrt(sum(x*x for x in e2)) or 1.0
            e2 = [x / n2 for x in e2]
            e3 = [e1n[1]*e2[2] - e1n[2]*e2[1],
                  e1n[2]*e2[0] - e1n[0]*e2[2],
                  e1n[0]*e2[1] - e1n[1]*e2[0]]
            return [e1n, e2, e3]

    def _matvec(self, R, v):
        # R columns are basis vectors; compute sum_i v[i] * R[:,i]
        n = len(v)
        out = [0.0]*n
        for i in range(n):
            for j in range(n):
                out[j] += R[i][j] * v[i]
        return out

    def _steer_clamped(self, from_pos, to_pos, bounds):
        import math
        dim = len(bounds)
        dist = math.dist(from_pos, to_pos)
        if dist <= self.step_size:
            cand = list(to_pos)
        else:
            r = self.step_size / max(dist, 1e-12)
            cand = [from_pos[d] + (to_pos[d] - from_pos[d]) * r for d in range(dim)]
        # Clamp within bounds
        for d in range(dim):
            lo, hi = 0.0, float(bounds[d])
            if cand[d] < lo: cand[d] = lo
            if cand[d] > hi: cand[d] = hi
        return tuple(cand)

    def _clamp_to_bounds(self, p, bounds):
        q = list(p)
        for d in range(len(bounds)):
            lo, hi = 0.0, float(bounds[d])
            if q[d] < lo: q[d] = lo
            if q[d] > hi: q[d] = hi
        return tuple(q)

    def _is_out_of_bounds(self, pos, bounds):
        for d in range(len(bounds)):
            if pos[d] < 0.0 or pos[d] > float(bounds[d]):
                return True
        return False

    def _shortcut_path(self, path, obstacles, is_3d, bounds, budget_sec=0.01, t0=None, limit=30.0):
        import random, time
        if not path or len(path) < 3:
            return path
        if t0 is None:
            t0 = time.time()
        pts = list(path)
        end_time = time.time() + budget_sec
        while time.time() < end_time and (time.time() - t0) < limit:
            i = random.randint(0, len(pts)-3)
            j = random.randint(i+2, len(pts)-1)
            a, b = pts[i], pts[j]
            # ensure within bounds and collision-free
            if self._is_out_of_bounds(a, bounds) or self._is_out_of_bounds(b, bounds):
                continue
            if not self._is_edge_in_obstacle(a, b, obstacles, is_3d, resolution=max(0.05, min(self.step_size/5.0, 0.3))):
                # replace middle segment
                pts = pts[:i+1] + pts[j:]
        return pts

    # ---------- Collision (given) ----------

    def _is_in_obstacle(self, pos, obstacles, is_3d):
        for obs in obstacles:
            if is_3d:
                x, y, z, w, h, d = obs
                px, py, pz = pos
                if x <= px <= x + w and y <= py <= y + h and z <= pz <= z + d:
                    return True
            else:
                x, y, w, h = obs
                px, py = pos
                if x <= px <= x + w and y <= py <= y + h:
                    return True
        return False

    def _is_edge_in_obstacle(self, from_pos, to_pos, obstacles, is_3d, resolution=1.0):
        import math
        distance = math.dist(from_pos, to_pos)
        steps = max(1, int(distance / resolution))
        if steps <= 1:
            return False
        # Skip endpoints to reduce boundary false positives
        for i in range(1, steps):
            interp = tuple(from_pos[d] + (to_pos[d] - from_pos[d]) * (i / steps) for d in range(len(from_pos)))
            if self._is_in_obstacle(interp, obstacles, is_3d):
                return True
        return False

'''

In [92]:
maps = [multi_obs_map, maze_map, narrow_map]
benchmarker = MultiMapBenchmarker(maps=maps, iter=100)

total_df = pd.DataFrame()
classic_method[5]['code'] = code
# for method in classic_method[:-2]:
for method in [classic_method[0], classic_method[4], classic_method[5]]:
    code_string = method['code']
    namedf = pd.DataFrame()
    namedf['alg_name'] = [method['algorithm']]* len(maps)
    with warnings.catch_warnings():
        warnings.simplefilter("ignore")
        planning_module = types.ModuleType("planning_module")
        exec(import_string+code_string, planning_module.__dict__)
        sys.modules[planning_module.__name__] = planning_module
        planner = planning_module.Planner(max_iter=5000)
        res, avg_rest = benchmarker.run(planner.plan)
        if method['algorithm'] == 'RRT':
            ref_avg = avg_rest
            outputs = []
        outputs = benchmarker.get_results()
        if avg_rest is None: continue
        imp_res = MultiMapBenchmarker.get_improvement(ref_avg, avg_rest)

        res_df = pd.concat([namedf, avg_rest, imp_res], axis=1)
        total_df = pd.concat([total_df, res_df], axis=0)

total_df


[2025.09.08 - 16:45:04] Map 1
Iteration 1: Time taken: 0.0251 seconds, Success: True
Iteration 2: Time taken: 0.0235 seconds, Success: True
Iteration 3: Time taken: 0.0204 seconds, Success: True
Iteration 4: Time taken: 0.0200 seconds, Success: True
Iteration 5: Time taken: 0.0120 seconds, Success: True
Iteration 6: Time taken: 0.0050 seconds, Success: True
Iteration 7: Time taken: 0.0177 seconds, Success: True
Iteration 8: Time taken: 0.0494 seconds, Success: True
Iteration 9: Time taken: 0.0258 seconds, Success: True
Iteration 10: Time taken: 0.0493 seconds, Success: True
Iteration 11: Time taken: 0.0349 seconds, Success: True
Iteration 12: Time taken: 0.0240 seconds, Success: True
Iteration 13: Time taken: 0.0226 seconds, Success: True
Iteration 14: Time taken: 0.0488 seconds, Success: True
Iteration 15: Time taken: 0.0296 seconds, Success: True
Iteration 16: Time taken: 0.0174 seconds, Success: True
Iteration 17: Time taken: 0.0151 seconds, Success: True
Iteration 18: Time taken: 0

alg_name  map_id  success_rate  time_avg  num_nodes_avg  path_length_avg  \
0      RRT       0           1.0  0.035874         461.98       188.080816   
1      RRT       1           1.0  0.210706        1637.59       303.968509   
2      RRT       2           1.0  0.072890         859.41       150.713378   
0   BI-RRT       0           1.0  0.002938          74.81       180.359506   
1   BI-RRT       1           1.0  0.009220         225.35       307.013373   
2   BI-RRT       2           1.0  0.007880         168.45       155.903769   
0  BI-RRT*       0           1.0  1.175311        3967.00       199.249278   
1  BI-RRT*       1           1.0  1.219959        4388.09       311.547932   
2  BI-RRT*       2           1.0  1.220694        4732.27       156.722399   

   smoothness_avg  success_improvement  time_improvement  length_improvement  \
0        0.006254                  0.0         -0.000000           -0.000000   
1        0.003852                  0.0         -0.000000           -0.000000   
2        0.007887                  0.0         -0.000000           -0.000000   
0        0.010692                  0.0         91.810418            4.105315   
1        0.006375                  0.0         95.624314           -1.001704   
2        0.013028                  0.0         89.189178           -3.443882   
0        0.009985                  0.0      -3176.240444           -5.938119   
1        0.006358                  0.0       -478.987621           -2.493490   
2        0.012816                  0.0      -1574.700818           -3.987052   

   smoothness_improvement  objective_score  
0                0.000000         0.000000  
1                0.000000         0.000000  
2                0.000000         0.000000  
0               70.977069        28.719074  
1               65.507041        28.814489  
2               65.183330        26.393894  
0               59.658876      -953.761463  
1               65.057896      -143.869695  
2               62.497377      -472.895169

In [93]:
# classic method result
grouped_avg = total_df.groupby('alg_name').mean()
a = pd.DataFrame(grouped_avg)
a

map_id  success_rate  time_avg  num_nodes_avg  path_length_avg  \
alg_name                                                                   
BI-RRT       1.0           1.0  0.006679     156.203333       214.425549   
BI-RRT*      1.0           1.0  1.205321    4362.453333       222.506536   
RRT          1.0           1.0  0.106490     986.326667       214.254234   

          smoothness_avg  success_improvement  time_improvement  \
alg_name                                                          
BI-RRT          0.010032                  0.0         92.207970   
BI-RRT*         0.009719                  0.0      -1743.309628   
RRT             0.005997                  0.0          0.000000   

          length_improvement  smoothness_improvement  objective_score  
alg_name                                                               
BI-RRT             -0.113424               67.222480        27.975819  
BI-RRT*            -4.139553               62.404716      -523.508775  
RRT                 0.000000                0.000000         0.000000

In [61]:
results = [outputs[35],outputs[195],outputs[265]]

In [62]:
for pmap, result in zip(maps, results):
    
    visualize_map_shapes(pmap.grid, obs=pmap.obstacles, start=pmap.start, goal=pmap.goal,
                        path=result.path, nodes=list(map(lambda x: x.position, result.nodes)), edges=result.edges)